In [2]:
from glob import glob
import string
from gensim import models
from gensim.corpora import Dictionary, MmCorpus
import nltk
from nltk.corpus import stopwords
from nltk import word_tokenize
from nltk.collocations import *
import pandas as pd
from langdetect import detect
from textblob import TextBlob
from pattern.fr import parse, split
import pattern.en
import funcy as fp
import re
import string

import pyLDAvis.gensim as gensimvis
import pyLDAvis
import unicodedata
import treetaggerwrapper

reviews=pd.read_csv('reviews.csv', encoding = 'utf-8')
reviews_en = reviews[reviews['language'] == 'en']
input_en = reviews_en.reviewDescription.str.cat(sep='. ')
reviews_fr = reviews[reviews['language'] == 'fr']
input_fr = reviews_fr.reviewDescription.str.cat(sep='. ')

In [43]:
import json
from os.path import join, dirname
from watson_developer_cloud import AlchemyLanguageV1

alchemy_language = AlchemyLanguageV1(api_key='c46619b5ff82334a6b5fff397ed6c5da94a611d8')

combined_operations = ['keyword', 'concept', 'taxonomy', 'doc-emotion']
result_en = alchemy_language.combined(text=input_en, extract=combined_operations)
result_fr = alchemy_language.combined(text=input_fr, extract=combined_operations)

In [46]:
print "ANGLAIS (", reviews_en.authorJob.count().sum(), " reviews )\n"
print reviews_en.groupby('company').reviewDescription.count().sort_values(ascending=False)
print "\nFRANCAIS (", reviews_fr.authorJob.count().sum(), " reviews )\n"
print reviews_fr.groupby('company').reviewDescription.count().sort_values(ascending=False)


print "ANGLAIS \n`\n"
print "### concepts detectés : ###\n"
for c in result_en['concepts']:
    print c['text'], ' (',c['relevance'],' )'

print "\n\n### mots clés detectés : ###\n"
for c in result_en['keywords']:
    print c['text'], ' (',c['relevance'],' )'

print "\n\n### taxonomies detectées : ###\n"
for c in result_en['taxonomy']:
    print c['label'], ' (',c['score'],' )'
    
print "\n\n\nFRANCAIS \n`\n"
print "### concepts detectés : ###\n"
for c in result_fr['concepts']:
    print c['text'], ' (',c['relevance'],' )'

print "\n\n### mots clés detectés : ###\n"
for c in result_fr['keywords']:
    print c['text'], ' (',c['relevance'],' )'
    
print "\n\n### taxonomies detectées : ###\n"
for c in result_fr['taxonomy']:
    print c['label'], ' (',c['score'],' )'

ANGLAIS ( 13107  reviews )

company
Accenture                       3226
Deloitte                        2723
Microsoft                       2107
EY                              1968
Google                          1051
Nissan North America             504
AXA Equitable Life Insurance     355
BNP Paribas                      299
Allianz Group                    237
EDF Renewable Energy             201
Air Liquide                      138
ALSTOM                           136
Renault                           78
Mazars                            33
PSA Peugeot Citroën               23
Thales                            16
LE GROUPE LA POSTE                13
Name: reviewDescription, dtype: int64

FRANCAIS ( 2021  reviews )

company
LE GROUPE LA POSTE              617
BNP Paribas                     288
PSA Peugeot Citroën             233
EDF Renewable Energy            228
Renault                         202
Thales                           75
ALSTOM                           72
Air Liqu

In [25]:

    
print "\n\n\nFRANCAIS \n`\n"
print "### concepts detectés : ###\n"
for c in result_fr['concepts']:
    print c['text'], ' (',c['relevance'],' )'

print "\n\n### mots clés detectés : ###\n"
for c in result_fr['keywords']:
    print c['text'], ' (',c['relevance'],' )'

Analysis and writing of macroscopic impact studies., 	Developing CICS Cobol, 	Realization of functional and technical recipes., 	Technical and functional analysis., 	Troubleshooting, punctual work, recurring work, Delivery., 	Analysis and development in Cobol (TP, Batch)
BONNE AMBIANCE DE TRAVAIL MAIS ORGANISATION ET TACHES DE TRAVAIL MAL REPARTIS
Great company to work for. ,Multiculture environment,International experience
My internship at BNP Paribas Securities Services as market data analyst allowed me to become familiar with leading financial providers and to build a market view on securities specificities.
Business and production focus,people are pleasant to work with,A day of business is pretty hectic lots of things going on ,I learn all technology that is not use anymore ETI on Unix


In [41]:
print "### concepts detectés : ###\n"

print labels[0]
print result_en[0]
print labels[2]
print result_en[2]

### concepts detectés : ###

Analysis and writing of macroscopic impact studies., 	Developing CICS Cobol, 	Realization of functional and technical recipes., 	Technical and functional analysis., 	Troubleshooting, punctual work, recurring work, Delivery., 	Analysis and development in Cobol (TP, Batch)
{u'status': u'OK', u'totalTransactions': u'4', u'language': u'english', u'taxonomy': [{u'confident': u'no', u'score': u'0.256718', u'label': u'/technology and computing/programming languages'}, {u'confident': u'no', u'score': u'0.155593', u'label': u'/business and industrial'}, {u'confident': u'no', u'score': u'0.137549', u'label': u'/technology and computing/software'}], u'keywords': [{u'relevance': u'0.973833', u'text': u'Developing CICS Cobol'}, {u'relevance': u'0.830176', u'text': u'macroscopic impact studies.'}, {u'relevance': u'0.538176', u'text': u'punctual work'}, {u'relevance': u'0.404131', u'text': u'technical recipes.'}, {u'relevance': u'0.399288', u'text': u'functional analysis.

In [56]:
for i in reviews.reviewDescription:
    print i

poste intéressant avec beaucoup de formations. bonne entente avec les collégues malgré une surcharge de travail.
il est agréable de travailler chez BNP Paribas mais dès que notre projet personnel prend le dessus sur le professionnel, cela ne convient pas forcément à la hiérarchie et ses plans de carrière.
J'y travaillais beaucoup, mais avec des personnes compétentes.
Equipe  sympa.,Ambiance correcte,Envoi de flux xml pour la reconnaissance documentaire et gestion des flux workflox.,RAD, LAD et workflow
Stage d'été agréable, des premières missions adaptées au niveau d'étude.
periode trop courte pour en juger.,Mais bonne experience,Bon retour
à l'agence de joinville le pont, l'environnement de travail était très agréable, une équipe jeune et soudé avec un très bonne état d'esprit.
Ma journée consistait à effectuer une surveillance et un compte rendu de toutes les alertes générées par les différentes applications,que gère la société BNP Paribas. Ainsi que de traiter tous les incidents de 